In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/projects/logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/projects/logical-reasoning/.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"


print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full None False datasets/mgtv results/mgtv-results_merged_model.csv


In [6]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 3.75 ms, sys: 6.43 ms, total: 10.2 ms
Wall time: 710 ms


In [7]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /Users/inflaton/code/engd/projects/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
MPS is available


In [8]:
%%time

model, tokenizer = load_model(model_name)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


loading model: llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 810 ms, sys: 3.84 s, total: 4.65 s
Wall time: 24.4 s


In [9]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [10]:
%%time

prompt1 = datasets["test"]["prompt"][1000]
print(prompt1)
print("--" * 20)
test_model(model, tokenizer, prompt1, device=device)

<s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难以理解，回答：问法错误
   - 若参与者提问基本还原了谜底真相，回答：回答正确
5. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。

请严格按照这些规则回答参与者提出的问题。

**谜面:** 在一个安静的夜晚，小村庄的湖边突然传来了阵阵哭泣声。第二天早晨，村长甄锐发现湖边的石头上放着一顶破旧的帽子，但没有人知道这顶帽子是从哪里来的，哭泣声又是为何。请还原故事真相。

**谜底:** 原来，这顶破旧的帽子属于一个小男孩，他小时候与爷爷在湖边生活。爷爷教他钓鱼、游泳，还告诉他湖中的海龟是他们的朋友。后来，小男孩随父母去了城市生活，但每年夏天都会回到村子探望爷爷。然而，去年夏天，爷爷因病去世，小男孩伤心欲绝。今年夏天，他回到村子，来到湖边，想起和爷爷的美好回忆，忍不住哭泣。他将爷爷的帽子放在湖边的石头上，希望能让爷爷的在天之灵得到安慰。那晚的哭泣声正是小男孩在祭莫他亲爱的爷爷。

**参与者提出的问题:** 哭泣和村庄有关系吗
<|im_end|>
<|im_start|>assistant

----------------------------------------
<s><s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一

In [11]:
%%time

eval_model(model, tokenizer, datasets["test"][:10], device=device)

 12%|█▎        | 1/8 [00:02<00:17,  2.47s/it]

--------
step 1: 不是</s>
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 8/8 [00:16<00:00,  2.09s/it]

CPU times: user 1.51 s, sys: 296 ms, total: 1.8 s
Wall time: 16.7 s


['不是', '是', '是', '是', '不是', '是', '不重要', '不是']

In [12]:
def evaluate_model(model, tokenizer, model_name, dataset):
    print("Evaluating model: " + model_name)
    predictions = eval_model(model, tokenizer, dataset, device=device)

    model_name += "_M3"

    save_results(
        model_name,
        results_path,
        dataset,
        predictions,
        debug=True,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=True)
    print(metrics)

In [13]:
%%time

evaluate_model(model, tokenizer, model_name, datasets["test"])

Evaluating model: llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full


  0%|          | 1/3000 [00:01<1:39:04,  1.98s/it]

--------
step 1: 不是</s>
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 3000/3000 [6:43:24<00:00,  8.07s/it]     

      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_NV4080  \
0                                                 不是                                   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_M3  \
0                                                 不是                               

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV4080  \
0                                                 不是                           

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_M3  
0                                                 不是                      
{'accuracy': 0.7853333333333333, 'incorrect_ids': [9, 24, 29, 31, 34, 36, 5

: 